In [1]:
import sys
sys.path.append("..") # Adds higher directory to python modules path.

%load_ext autoreload
%autoreload 2

In [2]:
import mplleaflet
import networkx as nx
import pandas as pd
import matplotlib.pyplot as plt
from collections import Counter

from osm2nx import read_osm, haversine
from graph import contract_edges, create_rpp_edgelist

from postman_problems.tests.utils import create_mock_csv_from_dataframe
from postman_problems.solver import rpp, cpp
from postman_problems.stats import calculate_postman_solution_stats

In [3]:
# load OSM to a directed NX
g_d = read_osm('sleepinggiant.osm')  

# create an undirected graph
g = g_d.to_undirected()

<class 'networkx.classes.digraph.DiGraph'>


#### Adding edges that don't exist on OSM, but should

In [4]:
g.add_edge('2318082790', '2318082832', id='white_horseshoe_fix_1')

#### Adding distance to OSM graph

In [5]:
for e in g.edges(data=True):
    e[2]['distance'] = haversine(g.node[e[0]]['lon'], 
                                 g.node[e[0]]['lat'], 
                                 g.node[e[1]]['lon'], 
                                 g.node[e[1]]['lat'])

## Create trail map only

In [6]:
g_t = g.copy()

for e in g.edges(data=True):
    
    # remove non trails
    name = e[2]['name'] if 'name' in e[2] else ''
    if ('Trail' not in name.split()):
        g_t.remove_edge(e[0], e[1])
        
    elif name is None:
        g_t.remove_edge(e[0], e[1])
        
    # remove non SG trails
    elif name in [
        'Farmington Canal Linear Trail', 
        'Farmington Canal Heritage Trail', 
        'Montowese Trail',
        '(white blazes)']:
        g_t.remove_edge(e[0], e[1])
        
for n in nx.isolates(g_t.copy()):
    g_t.remove_node(n)

## Viz Entire Map

In [7]:
fig, ax = plt.subplots(figsize=(1,8))

pos = {k: (g.node[k]['lon'], g.node[k]['lat']) for k in g.nodes()}    
nx.draw_networkx_edges(g, pos, width=4.0, edge_color='black', alpha=0.7)

mplleaflet.display(fig=ax.figure, tiles='cartodb_positron')

## Connect Edges

#### Add existing OSM edges to graph

In [8]:
edge_ids_to_add = [
    '223082783', 
    '223077827', 
    '40636272', 
    '223082785', 
    '222868698',
    '223083721',
    '222947116',
    '222711152',
    '222711155',
    '222860964',
    '223083718',
    '222867540',
    'white_horseshoe_fix_1'
]

edge_ids_to_remove = [
    '17220599'
]

In [9]:
for e in g.edges(data=True):
    way_id = e[2].get('id').split('-')[0]
    if way_id in edge_ids_to_add:
        g_t.add_edge(e[0], e[1], **e[2])
        g_t.add_node(e[0], lat=g.node[e[0]]['lat'], lon=g.node[e[0]]['lon'])
        g_t.add_node(e[1], lat=g.node[e[1]]['lat'], lon=g.node[e[1]]['lon'])
    if way_id in edge_ids_to_remove:
        if g_t.has_edge(e[0], e[1]):
            g_t.remove_edge(e[0], e[1])
            
for n in nx.isolates(g_t.copy()):
    g_t.remove_node(n)

## Viz Connected Component

In [10]:
fig, ax = plt.subplots(figsize=(1,12))

pos = {k: (g_t.node[k].get('lon'), g_t.node[k].get('lat')) for k in g_t.nodes()}    
nx.draw_networkx_edges(g_t, pos, width=4.0, edge_color='black', alpha=0.7)

pos_x = {k: (g_t.node[k]['lon'], g_t.node[k]['lat']) for k in g_t.nodes() if (g_t.degree(k)==1) | (g_t.degree(k)>2)}    
nx.draw_networkx_nodes(g_t, pos_x, nodelist=pos_x.keys(), node_size=30.0, node_color='red', alpha=0.7)

mplleaflet.display(fig=ax.figure, tiles='cartodb_positron')

## Viz Trail Color

In [300]:
name2color = {
    'Green Trail': 'green',
    'Quinnipiac Trail': 'blue',
    'Tower Trail': 'black',
    'Yellow Trail': 'yellow',
    'Red Square Trail': 'red',
    'White/Blue Trail Link': 'lightblue',
    'Orange Trail': 'orange',
    'Mount Carmel Avenue': 'black',
    'Violet Trail': 'violet',
    'blue Trail': 'blue',
    'Red Triangle Trail': 'red',
    'Blue Trail': 'blue',
    'Blue/Violet Trail Link': 'purple',
    'Red Circle Trail': 'red',
    'White Trail': 'gray',
    'Red Diamond Trail': 'red',
    'Yellow/Green Trail Link': 'yellowgreen',
    'Nature Trail': 'forestgreen',
    'Red Hexagon Trail': 'red',
    None: 'black'
}

In [312]:
fig, ax = plt.subplots(figsize=(1,10))
        
pos = {k: (g_t.node[k]['lon'], g_t.node[k]['lat']) for k in g_t.nodes()}   
e_color = [name2color[e[2].get('name')] for e in g_t.edges(data=True)]
nx.draw_networkx_edges(g_t, pos, width=3.0, edge_color=e_color, alpha=0.5)
nx.draw_networkx_nodes(g_t, pos_x, nodelist=pos_x.keys(), node_size=30.0, node_color='black', alpha=0.7)

mplleaflet.display(fig=ax.figure, tiles='cartodb_positron')

#### Check distance


In [12]:
sum([e[2]['distance']/1609.34 for e in g_t.edges(data=True)])

25.563014628288713

## Contract Edges

In [13]:
g_tc = nx.MultiGraph()

for ce in contract_edges(g_t, 'distance'):
    start_node, end_node, distance, path = ce
    
    contracted_edge = {
                'start_node': start_node,
                'end_node': end_node,
                'distance': distance,
                'name': g[path[0]][path[1]].get('name'),
                'required': 1,
                'path': path
            }
    
    g_tc.add_edge(start_node, end_node, **contracted_edge)
    g_tc.node[start_node]['lat'] = g.node[start_node]['lat']
    g_tc.node[start_node]['lon'] = g.node[start_node]['lon']
    g_tc.node[end_node]['lat'] = g.node[end_node]['lat']
    g_tc.node[end_node]['lon'] = g.node[end_node]['lon']

## Solve CPP

#### Create CPP edgelist

In [201]:
# create list with edge attributes and "from" & "to" nodes
tmp = []
for e in g_tc.edges(data=True):
    tmpi = e[2].copy()  # so we don't mess w original graph
    tmpi['start_node'] = e[0]
    tmpi['end_node'] = e[1]
    tmp.append(tmpi)

# create dataframe w node1 and node2 in order
eldf = pd.DataFrame(tmp)   
eldf = eldf[['start_node', 'end_node'] + list(set(eldf.columns)-{'start_node', 'end_node'})]
#eldf.drop('id', axis=1, inplace=True)

# create edgelist mock CSV
elfn = create_mock_csv_from_dataframe(eldf)

#### Solve CPP

In [202]:
circuit_cpp, gcpp = cpp(elfn, start_node='735393342')

In [203]:
calculate_postman_solution_stats(circuit_cpp)

OrderedDict([('distance_walked', 54522.94912134266),
             ('distance_doublebacked', 13383.367159452557),
             ('distance_walked_once', 41139.5819618901),
             ('distance_walked_optional', 0),
             ('distance_walked_required', 54522.94912134266),
             ('edges_walked', 170),
             ('edges_doublebacked', 46),
             ('edges_walked_once', 124),
             ('edges_walked_optional', 0),
             ('edges_walked_required', 170)])

## Solve RPP

In [ ]:
%%time
dfrpp = create_rpp_edgelist(g_tc, 
                            graph_full=g, 
                            edge_weight='distance', 
                            max_distance=2500)

In [232]:
# create mockfilename
elfn = create_mock_csv_from_dataframe(dfrpp)

In [233]:
Counter( dfrpp['required'])

Counter({0: 3034, 1: 124})

#### Solve RPP

In [234]:
%%time

# solve
circuit_rpp, grpp = rpp(elfn, start_node='735393342')

CPU times: user 5.43 s, sys: 35.5 ms, total: 5.47 s
Wall time: 5.52 s


In [235]:
len(circuit_rpp)

150

In [236]:
stats_rpp = calculate_postman_solution_stats(circuit_rpp)
stats_rpp

OrderedDict([('distance_walked', 49427.77406376237),
             ('distance_doublebacked', 8288.19210187231),
             ('distance_walked_once', 41139.581961890064),
             ('distance_walked_optional', 6015.881981594096),
             ('distance_walked_required', 43411.89208216828),
             ('edges_walked', 150),
             ('edges_doublebacked', 26),
             ('edges_walked_once', 124),
             ('edges_walked_optional', 13),
             ('edges_walked_required', 137)])

In [237]:
sum([e[3]['distance'] for e in circuit_rpp])/1609.34

30.713071236508366

## Viz RPP Solution

In [238]:
# hack to convert 'path' from str back to list.  Caused by `create_mock_csv_from_dataframe`
for e in circuit_rpp:
    if type(e[3]['path']) == str:
        exec('e[3]["path"]=' + e[3]["path"])

In [239]:
g_tcg = g_tc.copy()

# calc shortest path between optional nodes and add to graph
for e in circuit_rpp:
    granular_type = 'trail' if e[3]['required'] else 'optional'
    
    # add granular optional edges to g_tcg
    path = e[3]['path']
    for pair in list(zip(path[:-1], path[1:])):
        if (g_tcg.has_edge(pair[0], pair[1])) and (g_tcg[pair[0]][pair[1]][0].get('granular_type') == 'optional'):
                g_tcg[pair[0]][pair[1]][0]['granular_type'] = 'trail'
        else:
            g_tcg.add_edge(pair[0], pair[1], granular='True', granular_type=granular_type)
    
    # add granular nodes from optional edge paths to g_tcg
    for n in path:
        g_tcg.add_node(n, lat=g.node[n]['lat'], lon=g.node[n]['lon'])

### Viz: optional edges

In [240]:
fig, ax = plt.subplots(figsize=(1,8))

pos = {k: (g_tcg.node[k].get('lon'), g_tcg.node[k].get('lat')) for k in g_tcg.nodes()}    

el_opt = [e for e in g_tcg.edges(data=True) if e[2].get('granular_type') == 'optional'] 
nx.draw_networkx_edges(g_tcg, pos, edgelist=el_opt, width=6.0, edge_color='blue', alpha=1.0)

el_tr = [e for e in g_tcg.edges(data=True) if e[2].get('granular_type') == 'trail']
nx.draw_networkx_edges(g_tcg, pos, edgelist=el_tr, width=3.0, edge_color='black', alpha=0.8)

mplleaflet.display(fig=ax.figure, tiles='cartodb_positron')

### Viz: edges walked count

In [241]:
## Create graph directly from rpp_circuit and original graph w lat/lon (g)
color_seq = [None, 'black', 'magenta', 'orange', 'yellow']
grppviz = nx.MultiGraph()

for e in circuit_rpp:
    for n1, n2 in zip(e[3]['path'][:-1], e[3]['path'][1:]):
        if grppviz.has_edge(n1, n2):
            grppviz[n1][n2][0]['linewidth'] += 2
            grppviz[n1][n2][0]['cnt'] += 1
        else:                
            grppviz.add_edge(n1, n2, linewidth=2.5)
            grppviz[n1][n2][0]['color_st'] = 'black' if g_t.has_edge(n1, n2) else 'red'
            grppviz[n1][n2][0]['cnt'] = 1
            grppviz.add_node(n1, lat=g.node[n1]['lat'], lon=g.node[n1]['lon'])
            grppviz.add_node(n2, lat=g.node[n2]['lat'], lon=g.node[n2]['lon']) 

for e in grppviz.edges(data=True):
    e[2]['color_cnt'] = color_seq[1] if 'cnt' not in e[2] else color_seq[e[2]['cnt'] ]
    

In [242]:
fig, ax = plt.subplots(figsize=(1,10))

pos = {k: (grppviz.node[k]['lon'], grppviz.node[k]['lat']) for k in grppviz.nodes()}    
e_width = [e[2]['linewidth'] for e in grppviz.edges(data=True)]
e_color = [e[2]['color_cnt'] for e in grppviz.edges(data=True)]
nx.draw_networkx_edges(grppviz, pos, width=e_width, edge_color=e_color, alpha=0.7)

mplleaflet.display(fig=ax.figure, tiles='cartodb_positron')

In [199]:
Counter(Counter([tuple(sorted([e[0], e[1]])) for e in circuit_rpp]).values())

Counter({1: 87, 2: 39})

## Create Geojson solution

In [314]:
geojson = {'features':[], 'type': 'FeatureCollection'}
time = 0
path = list(reversed(circuit_rpp[0][3]['path']))

for e in circuit_rpp:
    if e[3]['path'][0] != path[-1]: 
        path = list(reversed(e[3]['path']))
    else:
        path = e[3]['path']
    
    for n in path:
        time += 1
        doc = {'type': 'Feature',
              'properties': {
                  'latitude': g.node[n]['lat'],
                  'longitude': g.node[n]['lon'],
                  'time': time,
                  'id': e[3].get('id')
              },
              'geometry':{
                  'type': 'Point',
                  'coordinates': [g.node[n]['lon'], g.node[n]['lat']]
              }
          }
        geojson['features'].append(doc)
        

In [289]:
with open('circuit_rpp.geojson','w') as f:
    json.dump(geojson, f)